In [1]:
import pandas as pd
import numpy as np

# get incident case data
url = 'https://media.githubusercontent.com/media/reichlab/covid19-forecast-hub/master/data-truth/truth-Incident%20Cases.csv'
raw_cases = pd.read_csv(url)
#raw_cases

# get incident hospitalization data
url = 'https://media.githubusercontent.com/media/reichlab/covid19-forecast-hub/master/data-truth/truth-Incident%20Hospitalizations.csv'
raw_hosp = pd.read_csv(url)
#raw_hosp

# get cumulative death data
url = 'https://media.githubusercontent.com/media/reichlab/covid19-forecast-hub/master/data-truth/truth-Cumulative%20Deaths.csv'
raw_deaths = pd.read_csv(url)
raw_deaths

/var/folders/z_/l_q4g1892pqd5g0p2z2f66_m0000gn/T/ipykernel_25245/3057209147.py:6: DtypeWarning: Columns (1) have mixed types. Specify dtype option on import or set low_memory=False.
  raw_cases = pd.read_csv(url)
/var/folders/z_/l_q4g1892pqd5g0p2z2f66_m0000gn/T/ipykernel_25245/3057209147.py:16: DtypeWarning: Columns (1) have mixed types. Specify dtype option on import or set low_memory=False.
  raw_deaths = pd.read_csv(url)


date location   location_name    value
0        2020-01-22     1001  Autauga County        0
1        2020-01-23     1001  Autauga County        0
2        2020-01-24     1001  Autauga County        0
3        2020-01-25     1001  Autauga County        0
4        2020-01-26     1001  Autauga County        0
...             ...      ...             ...      ...
3641595  2023-02-28       US   United States  1120002
3641596  2023-03-01       US   United States  1120911
3641597  2023-03-02       US   United States  1121667
3641598  2023-03-03       US   United States  1122157
3641599  2023-03-04       US   United States  1122164

[3641600 rows x 4 columns]

In [7]:
# incident to census function
def incident_to_census(data, duration):
    '''This function converts incident data to census data.
    
    :param data: data must be a DataFrame with a census and value column, where value column corresponds to incident data
    :param duration: this is the length of time before leaving state variable category
    :returns: DataFrame with census column filled out
    '''
    for i in range(0, len(data.index) - duration):
        for j in range(0, duration + 1):
            data.census[i + j] += data.value[i]
            
        data.census[i + duration] -= data.value[i]

    for i in range(len(data.index) - duration, len(data.index)):
        rows_left = len(data.index) - i
        for j in range(0, rows_left):
            data.census[i + j] += data.value[i]
        
    return data

In [6]:
raw_cases['date'] = pd.to_datetime(raw_cases.date, infer_datetime_format = True)
raw_cases.sort_values(by = 'date', ascending = True, inplace = True)
display(raw_cases.head())

raw_hosp['date'] = pd.to_datetime(raw_hosp.date, infer_datetime_format = True)
raw_hosp.sort_values(by = 'date', ascending = True, inplace = True)
display(raw_hosp.head())

raw_deaths['date'] = pd.to_datetime(raw_deaths.date, infer_datetime_format = True)
raw_deaths.sort_values(by = 'date', ascending = True, inplace = True)
display(raw_deaths.head())

/var/folders/z_/l_q4g1892pqd5g0p2z2f66_m0000gn/T/ipykernel_25245/151587554.py:1: UserWarning: The argument 'infer_datetime_format' is deprecated and will be removed in a future version. A strict version of it is now the default, see https://pandas.pydata.org/pdeps/0004-consistent-to-datetime-parsing.html. You can safely remove this argument.
  raw_cases['date'] = pd.to_datetime(raw_cases.date, infer_datetime_format = True)


date location   location_name  value
0      2020-01-22     1001  Autauga County      0
702146 2020-01-22    17043   DuPage County      0
703284 2020-01-22    17045    Edgar County      0
704422 2020-01-22    17047  Edwards County      0
687352 2020-01-22    17017     Cass County      0

/var/folders/z_/l_q4g1892pqd5g0p2z2f66_m0000gn/T/ipykernel_25245/151587554.py:5: UserWarning: The argument 'infer_datetime_format' is deprecated and will be removed in a future version. A strict version of it is now the default, see https://pandas.pydata.org/pdeps/0004-consistent-to-datetime-parsing.html. You can safely remove this argument.
  raw_hosp['date'] = pd.to_datetime(raw_hosp.date, infer_datetime_format = True)


date location location_name  value
13332 2020-01-01       32        Nevada    132
13619 2020-01-02       32        Nevada    132
14629 2020-01-03       32        Nevada    132
12644 2020-01-03       05      Arkansas      0
13597 2020-01-04       05      Arkansas      0

/var/folders/z_/l_q4g1892pqd5g0p2z2f66_m0000gn/T/ipykernel_25245/151587554.py:9: UserWarning: The argument 'infer_datetime_format' is deprecated and will be removed in a future version. A strict version of it is now the default, see https://pandas.pydata.org/pdeps/0004-consistent-to-datetime-parsing.html. You can safely remove this argument.
  raw_deaths['date'] = pd.to_datetime(raw_deaths.date, infer_datetime_format = True)


date location   location_name  value
0      2020-01-22     1001  Autauga County      0
702146 2020-01-22    17043   DuPage County      0
703284 2020-01-22    17045    Edgar County      0
704422 2020-01-22    17047  Edwards County      0
687352 2020-01-22    17017     Cass County      0

In [36]:
raw_hosp.date[1]

Timestamp('2021-02-24 00:00:00')

In [45]:
us_hosp = raw_hosp.groupby(["date"]).sum()
us_hosp

location   
date                                                            
2020-01-01                                                 32  \
2020-01-02                                                 32   
2020-01-03                                               3205   
2020-01-04                                               0532   
2020-01-05                                               3205   
...                                                       ...   
2023-04-11  221526110917283747461202US54395536210472012430...   
2023-04-12  2646134908342028427256604178164021372701253348...   
2023-04-13  3641261024490944603427065121504730041553464254...   
2023-04-14  US28153878301247421117345055044539222006511846...   
2023-04-15  3416062546380455300227205111214254455648601509...   

                                                location_name  value  
date                                                                  
2020-01-01                                             Nevada    132  
2020-01-02                                             Nevada    132  
2020-01-03                                     NevadaArkansas    132  
2020-01-04                                     ArkansasNevada    132  
2020-01-05                                     NevadaArkansas    132  
...                                                       ...    ...  
2023-04-11  LouisianaHawaiiMichiganDistrict of ColumbiaCon...   4056  
2023-04-12  MichiganSouth DakotaGeorgiaUtahColoradoNew Jer...   4112  
2023-04-13  New YorkOregonMichiganDelawareMarylandUtahConn...   4128  
2023-04-14  United StatesMississippiHawaiiNorth DakotaVirg...   4084  
2023-04-15  New JerseyIdahoCaliforniaMassachusettsSouth Da...   4052  

[1118 rows x 3 columns]

In [11]:
us_deaths = raw_deaths[raw_deaths["location"] == "US"]
us_deaths

date location  location_name    value
3640462 2020-01-22       US  United States        1
3640463 2020-01-23       US  United States        1
3640464 2020-01-24       US  United States        1
3640465 2020-01-25       US  United States        1
3640466 2020-01-26       US  United States        1
...            ...      ...            ...      ...
3641595 2023-02-28       US  United States  1120002
3641596 2023-03-01       US  United States  1120911
3641597 2023-03-02       US  United States  1121667
3641598 2023-03-03       US  United States  1122157
3641599 2023-03-04       US  United States  1122164

[1138 rows x 4 columns]

In [8]:
us_cases1 = raw_cases[raw_cases["location"] == "US"]
us_cases1
us_cases = us_cases1
infectious_period = 10
us_cases["infectious_period"] = infectious_period
us_cases["census"] = 0
us_cases = us_cases.reset_index()
us_cases

cases_census = incident_to_census(us_cases, infectious_period)

/var/folders/z_/l_q4g1892pqd5g0p2z2f66_m0000gn/T/ipykernel_25245/2410222144.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  us_cases["infectious_period"] = infectious_period
/var/folders/z_/l_q4g1892pqd5g0p2z2f66_m0000gn/T/ipykernel_25245/2410222144.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  us_cases["census"] = 0
/var/folders/z_/l_q4g1892pqd5g0p2z2f66_m0000gn/T/ipykernel_25245/3693494762.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [10]:
from IPython.display import HTML 
HTML(cases_census.to_html())

## Function to convert incident to census data 

In [15]:
us_hosp1 = raw_hosp[raw_hosp["location"] == "US"]
us_hosp1
us_hosp = us_hosp1
length_of_stay = 6
us_hosp["length_of_stay"] = length_of_stay
us_hosp["census"] = 0
us_hosp = us_hosp.reset_index()
us_hosp
mo_hosp = us_hosp.copy()
mo_hosp["value"] = 1

hosp_census = incident_to_census(us_hosp, length_of_stay)

/var/folders/z_/l_q4g1892pqd5g0p2z2f66_m0000gn/T/ipykernel_25245/2056305948.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  us_hosp["length_of_stay"] = length_of_stay
/var/folders/z_/l_q4g1892pqd5g0p2z2f66_m0000gn/T/ipykernel_25245/2056305948.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  us_hosp["census"] = 0
/var/folders/z_/l_q4g1892pqd5g0p2z2f66_m0000gn/T/ipykernel_25245/3693494762.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats 

/var/folders/z_/l_q4g1892pqd5g0p2z2f66_m0000gn/T/ipykernel_25245/3693494762.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data.census[i + duration] -= data.value[i]
/var/folders/z_/l_q4g1892pqd5g0p2z2f66_m0000gn/T/ipykernel_25245/3693494762.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data.census[i + j] += data.value[i]
/var/folders/z_/l_q4g1892pqd5g0p2z2f66_m0000gn/T/ipykernel_25245/3693494762.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#return

In [16]:
from IPython.display import HTML 
HTML(hosp_census.to_html())

In [17]:
us_hosp.to_csv('us_hospitalization_census_and_incident_data.csv', columns=["date", "location", "length_of_stay", "value", "census"], 
              header=["date", "location", "length_of_stay", "admissions", "hospital_census"])

In [18]:
us_cases.to_csv('us_case_census_and_incident_data.csv', columns=["date", "location", "infectious_period", "value", "census"], 
              header=["date", "location", "infectious_period", "new_cases", "case_census"])

In [19]:
us_deaths.to_csv('us_cumulative_death_data.csv', columns=["date", "location", "value"], 
              header=["date", "location", "cumulative_deaths"])

In [67]:
2026 + 8598 - 1761

8863

In [75]:
for i in range(0, length_of_stay):
    print(i)

0
1
2
3
4
5


In [3]:
raw_cases

date location   location_name  value
0        2020-01-22     1001  Autauga County      0
1        2020-01-23     1001  Autauga County      0
2        2020-01-24     1001  Autauga County      0
3        2020-01-25     1001  Autauga County      0
4        2020-01-26     1001  Autauga County      0
...             ...      ...             ...    ...
3641595  2023-02-28       US   United States  42553
3641596  2023-03-01       US   United States  83376
3641597  2023-03-02       US   United States  61160
3641598  2023-03-03       US   United States  60103
3641599  2023-03-04       US   United States   1932

[3641600 rows x 4 columns]